In [1]:
import calliope
import pandas as pd
import plotly.express as px 


In [6]:
model = calliope.Model('./model.yaml', scenario = "sensitivity_battery_capacity_200") #, scenario = "base")
model.build()
model.solve()
#model.to_netcdf("./model.nc")
#calligraph 

KeyboardInterrupt: 

In [3]:
model.inputs

<xarray.Dataset> Size: 60MB
Dimensions:                       (costs: 3, techs: 17, nodes: 7, carriers: 3,
                                   timesteps: 8760)
Coordinates:
  * techs                         (techs) object 136B 'battery' ... 'unmet_de...
  * carriers                      (carriers) <U8 96B 'power' ... 'power_pv'
  * nodes                         (nodes) object 56B 'e1_1' ... 'transformer'
  * timesteps                     (timesteps) datetime64[ns] 70kB 2023-01-01 ...
  * costs                         (costs) object 24B 'co2_emissions' ... 'tra...
Data variables: (12/30)
    bigM                          float64 8B 1e+06
    objective_cost_weights        (costs) float64 24B 0.173 0.671 0.156
    base_tech                     (techs) object 136B 'storage' ... 'supply'
    carrier_in                    (nodes, techs, carriers) float64 3kB 1.0 .....
    carrier_out                   (nodes, techs, carriers) float64 3kB 1.0 .....
    color                         (techs) object 136B '#be82ff' ... '#d62128'
    ...                            ...
    cost_flow_in                  (costs, timesteps, techs, nodes) float64 25MB ...
    source_use_equals             (timesteps, techs) float64 1MB nan nan ... nan
    sink_use_equals               (timesteps, nodes, techs) float64 8MB nan ....
    definition_matrix             (nodes, techs, carriers) bool 357B True ......
    timestep_resolution           (timesteps) float64 70kB 1.0 1.0 ... 1.0 1.0
    timestep_weights              (timesteps) float64 70kB 1.0 1.0 ... 1.0 1.0
Attributes: (12/16)
    termination_condition:         optimal
    calliope_version_defined:      0.7.0
    calliope_version_initialised:  0.7.0.dev4
    applied_overrides:             base_setting
    scenario:                      base
    defaults:                      {'bigM': 1000000000.0, 'objective_cost_wei...
    ...                            ...
    name:                          Generic Urban Community
    timestamp_model_creation:      1735842445.429391
    timestamp_build_start:         1735842449.877211
    timestamp_build_complete:      1735842502.06932
    timestamp_solve_start:         1735842502.069656
    timestamp_solve_complete:      1735842536.46639

In [4]:
model.results

<xarray.Dataset> Size: 167MB
Dimensions:                      (nodes: 7, techs: 17, carriers: 3,
                                  timesteps: 8760, costs: 3)
Coordinates:
  * techs                        (techs) object 136B 'battery' ... 'unmet_dem...
  * carriers                     (carriers) <U8 96B 'power' ... 'power_pv'
  * nodes                        (nodes) object 56B 'e1_1' ... 'transformer'
  * timesteps                    (timesteps) datetime64[ns] 70kB 2023-01-01 ....
  * costs                        (costs) object 24B 'co2_emissions' ... 'tran...
Data variables: (12/19)
    flow_cap                     (nodes, techs, carriers) float64 3kB 43.32 ....
    link_flow_cap                (techs) float64 136B nan nan nan ... 0.0 nan
    flow_out                     (nodes, techs, carriers, timesteps) float64 25MB ...
    flow_in                      (nodes, techs, carriers, timesteps) float64 25MB ...
    source_use                   (nodes, techs, timesteps) float64 8MB nan .....
    source_cap                   (nodes, techs) float64 952B nan nan ... nan nan
    ...                           ...
    cost_investment              (nodes, techs, costs) float64 3kB nan ... nan
    cost                         (nodes, techs, costs) float64 3kB nan ... nan
    capacity_factor              (nodes, techs, carriers, timesteps) float64 25MB ...
    systemwide_capacity_factor   (techs, carriers) float64 408B 0.2114 ... 0.0
    systemwide_levelised_cost    (carriers, techs, costs) float64 1kB nan ......
    total_levelised_cost         (carriers, costs) float64 72B 0.1223 ... 0.0...
Attributes: (12/16)
    termination_condition:         optimal
    calliope_version_defined:      0.7.0
    calliope_version_initialised:  0.7.0.dev4
    applied_overrides:             base_setting
    scenario:                      base
    defaults:                      {'bigM': 1000000000.0, 'objective_cost_wei...
    ...                            ...
    name:                          Generic Urban Community
    timestamp_model_creation:      1735842445.429391
    timestamp_build_start:         1735842449.877211
    timestamp_build_complete:      1735842502.06932
    timestamp_solve_start:         1735842502.069656
    timestamp_solve_complete:      1735842536.46639

In [5]:
model.results.flow_in.to_series()

nodes        techs         carriers  timesteps          
e1_1         battery       power     2023-01-01 00:00:00    0.037574
                                     2023-01-01 01:00:00    0.011951
                                     2023-01-01 02:00:00    0.011633
                                     2023-01-01 03:00:00    0.027743
                                     2023-01-01 04:00:00    0.025619
                                                              ...   
transformer  unmet_demand  power_pv  2023-12-31 19:00:00         NaN
                                     2023-12-31 20:00:00         NaN
                                     2023-12-31 21:00:00         NaN
                                     2023-12-31 22:00:00         NaN
                                     2023-12-31 23:00:00         NaN
Name: flow_in, Length: 3127320, dtype: float64

In [6]:
costs = model.results.cost_var.to_series().dropna()
print(costs)

cost_sums = costs.groupby(level='costs').sum()
print(cost_sums)

nodes        techs            costs                             timesteps          
e1_1         curtailment      monetary                          2023-01-01 00:00:00    0.000000
                                                                2023-01-01 01:00:00    0.000000
                                                                2023-01-01 02:00:00    0.000000
                                                                2023-01-01 03:00:00    0.000000
                                                                2023-01-01 04:00:00    0.000000
                                                                                         ...   
transformer  transformer_out  transformer_congestion_indicator  2023-12-31 19:00:00    0.000151
                                                                2023-12-31 20:00:00    0.000151
                                                                2023-12-31 21:00:00    0.000151
                                                    

In [7]:
filtered_costs = costs.loc[
    (costs.index.get_level_values('techs').isin(['transformers', 'transformers_sell'])) &
    (costs.index.get_level_values('costs') == 'importance')
]

In [8]:
colors = model.inputs.color.to_series().to_dict()

df_electricity = (
    (model.results.flow_out.fillna(0) - model.results.flow_in.fillna(0))
    .sel(carriers="power")
    .sum("nodes")
    .to_series()
    .where(lambda x: x != 0)
    .dropna()
    .to_frame("Flow in/out (kWh)")
    .reset_index()
)

df_electricity.head()

df_electricity_demand = df_electricity[df_electricity.techs == "demand_power"]
df_electricity_other = df_electricity[df_electricity.techs != "demand_power"]

df_electricity_other.head()

techs           timesteps  Flow in/out (kWh)
0  battery 2023-01-01 00:00:00          -0.182977
1  battery 2023-01-01 01:00:00          -0.053082
2  battery 2023-01-01 02:00:00          -0.052637
3  battery 2023-01-01 03:00:00          -0.133175
4  battery 2023-01-01 04:00:00          -0.123489

In [9]:
fig1 = px.bar(
    df_electricity_other,
    x="timesteps",
    y="Flow in/out (kWh)",
    color="techs",
    color_discrete_map=colors,
)
fig1.add_scatter(
    x=df_electricity_demand.timesteps,
    y=-1 * df_electricity_demand["Flow in/out (kWh)"],
    marker_color="black",
    name="demand",
)

In [10]:
df_HV = (
    (model.results.flow_out.fillna(0) - model.results.flow_in.fillna(0))
    .sel(carriers="power_MV")
    .sum("nodes")
    .to_series()
    .where(lambda x: x != 0)
    .dropna()
    .to_frame("Flow in/out (kWh)")
    .reset_index()
)

df_HV_demand = df_HV[df_HV.techs == "demand_power"]
df_HV_other = df_HV[df_HV.techs != "demand_power"]

df_HV_other.head()

fig1 = px.bar(
    df_HV_other,
    x="timesteps",
    y="Flow in/out (kWh)",
    color="techs",
    color_discrete_map=colors,
)
fig1.add_scatter(
    x=df_HV_demand.timesteps,
    y=-1 * df_electricity_demand["Flow in/out (kWh)"],
    marker_color="black",
    name="demand",
)

In [11]:
df_pv = (
    (model.results.flow_out.fillna(0) - model.results.flow_in.fillna(0))
    .sel(carriers="power_pv")
    .sum("nodes")
    .to_series()
    .where(lambda x: x != 0)
    .dropna()
    .to_frame("Flow in/out (kWh)")
    .reset_index()
)

df_HV_demand = df_pv[df_pv.techs == "demand_power"]
df_HV_other = df_pv[df_pv.techs != "demand_power"]

df_HV_other.head()

fig1 = px.bar(
    df_HV_other,
    x="timesteps",
    y="Flow in/out (kWh)",
    color="techs",
    color_discrete_map=colors,
)
fig1.add_scatter(
    x=df_HV_demand.timesteps,
    y=-1 * df_electricity_demand["Flow in/out (kWh)"],
    marker_color="black",
    name="demand",
)
    

In [12]:
import xarray as xr
import pandas as pd
import plotly.express as px

# ----------------------------
# 📂 Dataset Loading
# ----------------------------
# Replace with your dataset loading command if needed
dataset = model.results  

# ----------------------------
# 🛠️ Data Processing
# ----------------------------
# Extract installed capacity from `flow_cap` and format as DataFrame
df_capacity = (
    dataset["flow_cap"]
    .sum(dim="nodes")  # Aggregate across all nodes
    .to_dataframe(name="installed_capacity")  # Name the capacity column
    .reset_index()  # Flatten the index
)

# Define technology groups
selected_techs_power_pv = ["solar_power", "curtailment"]  # PV-related techs
selected_techs_power_lv = ["pv", "battery"]  # LV grid technologies
selected_techs_power_mv = ["sell_grid_power", "supply_grid_power", "battery_central"]  # MV grid technologies

# Filter relevant technologies
df_filtered = df_capacity[
    df_capacity["techs"].isin(
        selected_techs_power_pv + selected_techs_power_lv + selected_techs_power_mv
    )
]

# Handle PV explicitly (adjust capacity)
df_pv = df_filtered[df_filtered["techs"] == "pv"].groupby("techs", as_index=False).agg(
    {"installed_capacity": "sum"}
)
df_pv["installed_capacity"] = df_pv["installed_capacity"] / 2  # Adjust PV duplication
df_pv["carrier_type"] = "Power LV"

# Remove original PV entries and merge adjusted PV back
df_filtered = df_filtered[df_filtered["techs"] != "pv"]
df_final = pd.concat([df_filtered, df_pv], ignore_index=True)

# Add carrier type based on technology groups
df_final["carrier_type"] = df_final["techs"].apply(
    lambda x: "Power PV" if x in selected_techs_power_pv
    else "Power LV" if x in selected_techs_power_lv
    else "Power MV" if x in selected_techs_power_mv
    else "Other"
)

# Replace technology names for clarity
tech_names = {
    "supply_grid_power": "Grid buy",
    "solar_power": "Solar power",
    "unmet_demand": "Unmet demand",
    "demand_power": "Power demand",
    "sell_grid_power": "Grid sell",
    "curtailment": "Curtailment",
    "transformer_in": "Transformer in",
    "transformer_out": "Transformer out",
    "pv": "PV",
    "battery": "Battery storage",
    "battery_central": "Central Battery storage"
}

df_final["techs"] = df_final["techs"].map(tech_names).fillna(df_final["techs"])

# ----------------------------
# 🎨 Visualization with Plotly
# ----------------------------
# Color mapping aligned with your Accenture specifications
tech_colors = {
    "Grid buy": "#96968c",
    "Solar power": "#942adf",
    "Unmet demand": "#d62128",
    "Power demand": "#000000",
    "Grid sell": "#e6e6dc",
    "Curtailment": "#b03060",
    "Transformer in": "#756584",
    "Transformer out": "#756584",
    "PV": "#460073",
    "Battery storage": "#5a0a4f",
    "Central Battery storage": "#5a0a3f"
}

fig = px.bar(
    df_final,
    x="carrier_type",
    y="installed_capacity",
    color="techs",  # Differentiate by technology
    text="installed_capacity",  # Display capacity values on bars
    labels={
        "installed_capacity": "Installed Capacity (kW)",
        "techs": "Technology",
        "carrier_type": "Power Carrier"
    },
    title="Installed Capacity by Technology and Carrier (Stacked)",
    barmode="stack",  # Stacked bars for grouped categories
    text_auto=True,  # Automatically format text labels
    color_discrete_map=tech_colors  # Apply custom colors
)

# ----------------------------
# ✏️ Styling and Layout
# ----------------------------
fig.update_layout(
    title_font=dict(size=20, family="Arial", color="black"),
    xaxis_title_font=dict(size=14),
    yaxis_title_font=dict(size=14),
    legend_title_font=dict(size=12),
    legend=dict(font=dict(size=10)),
    bargap=0.15,  # Slight gap between bars
    width=900,
    height=600,
    plot_bgcolor="white"
)

# Improve text readability on bars
fig.update_traces(
    textfont_size=12,
    textposition='inside'
)

# Grid styling
fig.update_xaxes(showgrid=False)
fig.update_yaxes(showgrid=True, gridcolor='lightgrey', gridwidth=0.5)

# Show the plot
fig.show()


In [13]:
import xarray as xr
import pandas as pd
import plotly.express as px
import numpy as np

# ----------------------------
# 📂 Dataset Loading
# ----------------------------
# Replace with your dataset loading command if needed
dataset = model.results  

# ----------------------------
# 🛠️ Data Processing
# ----------------------------
# Extract and process flows for key technologies
def get_sorted_flow(dataset, tech, direction="flow_out"):
    """
    Retrieve and sort flow data for a specific technology and direction.
    """
    try:
        data = dataset[direction].sel(techs=tech).sum(dim='nodes').fillna(0)
        df = data.to_pandas()
        if len(df.shape) > 1:
            df = df.sum(axis=0)
        return df.sort_values(ascending=False).reset_index(drop=True)
    except KeyError:
        print(f"[WARNING] Technology '{tech}' not found in dataset.")
        return pd.Series(dtype='float64')

# Retrieve sorted flows for each key technology
flows = {
    "transformer_in": get_sorted_flow(dataset, 'transformer_in'),
    "transformer_out": get_sorted_flow(dataset, 'transformer_out'),
    "pv": get_sorted_flow(dataset, 'pv'),
    "battery_in": get_sorted_flow(dataset, 'battery', direction='flow_in'),
    "battery_out": get_sorted_flow(dataset, 'battery', direction='flow_out')
}

# Create x-axis for each technology's duration curve
x_axes = {key: np.linspace(0, len(flow) - 1, len(flow)) for key, flow in flows.items() if not flow.empty}

# Flatten data for Plotly
df_duration_curve = pd.concat([
    pd.DataFrame({"Time Step": x_axes[key], "Flow (kW)": flow, "Technology": key})
    for key, flow in flows.items() if not flow.empty
], ignore_index=True)

# Replace technology names with readable labels
tech_names = {
    "transformer_in": "Transformer in",
    "transformer_out": "Transformer out",
    "pv": "PV",
    "battery_in": "Battery charge",
    "battery_out": "Battery discharge"
}

df_duration_curve["Technology"] = df_duration_curve["Technology"].map(tech_names).fillna(df_duration_curve["Technology"])

# ----------------------------
# 🎨 Visualization with Plotly
# ----------------------------
# Color mapping aligned with your Accenture specifications
tech_colors = {
    "Transformer in": "#756584",
    "Transformer out": "#756584",
    "PV": "#460073",
    "Battery charge": "#5a0a4f",
    "Battery discharge": "#5a0a3f"
}

fig = px.line(
    df_duration_curve,
    x="Time Step",
    y="Flow (kW)",
    color="Technology",
    labels={
        "Time Step": "Time Step (Sorted by Load or Output)",
        "Flow (kW)": "Flow (kW)",
        "Technology": "Technology"
    },
    title="Load Duration Curve for Key Technologies",
    color_discrete_map=tech_colors,
    line_shape="linear"
)

# ----------------------------
# ✏️ Styling and Layout
# ----------------------------
fig.update_layout(
    title_font=dict(size=20, family="Arial", color="black"),
    xaxis_title_font=dict(size=14),
    yaxis_title_font=dict(size=14),
    legend_title_font=dict(size=12),
    legend=dict(font=dict(size=10)),
    width=900,
    height=600,
    plot_bgcolor="white"
)

# Grid styling
fig.update_xaxes(showgrid=True, gridcolor='lightgrey', gridwidth=0.5)
fig.update_yaxes(showgrid=True, gridcolor='lightgrey', gridwidth=0.5)

# Show the plot
fig.show()


Umet Demand